# How to use ImageOverlay

It may happen that you want to draw an image on you map. Here are example on how to do that.

In [1]:
from branca.six import PY3

import folium
from folium import plugins

## In importing a PNG

If you have a static image file on your disk, you can simply draw it on the map in doing:

In [2]:
m = folium.Map([37,0], zoom_start=1, tiles='stamentoner')

plugins.ImageOverlay(open('Mercator_projection_SW.png',
                          'br' if PY3 else 'r'),
                    [[-82,-180],[82,180]],
                    opacity=0.8,
                   ).add_to(m)

folium.LayerControl().add_to(m)
m

A few remarks:

* Note that your image has to be in Mercator projection format.

  The image we've used is based on https://en.wikipedia.org/wiki/File:Mercator_projection_SW.jpg ; that you can find in wikipedia's article on Mercator Projection (https://en.wikipedia.org/wiki/Mercator_projection).


* In python 3, be careful to mention explictely the `read mode` of the file (`open(..., 'rb')`). You'll get an error otherwise. 

You can also provide simply a file name. In this case, the image will not be embedded in folium's output : you'll need to keep it on your server when your map will be deployed.

In [3]:
m = folium.Map([37,0], zoom_start=1, tiles='stamentoner')

plugins.ImageOverlay('Mercator_projection_SW.png',
                    [[-82,-180],[82,180]],
                    opacity=0.8,
                   ).add_to(m)

folium.LayerControl().add_to(m)
m

## In importing a JPG

This works exactly the same way if you want to put a JPG intead of a PNG.

In [4]:
m = folium.Map([37,0], zoom_start=1, tiles='stamentoner')

plugins.ImageOverlay(open('Mercator_projection_SW.jpg',
                          'br' if PY3 else 'r'),
                    [[-82,-180],[82,180]],
                    opacity=0.8,
                   ).add_to(m)

folium.LayerControl().add_to(m)
m

## In creating an image with numpy

Now you may wish to create your own image, based on another python computation.
For this, you'll need to have numpy installed on your machine.

In [5]:
import numpy as np

Let's creater an image to draw a rectangle in the bounds [[0,-60],[60,60]]

In [6]:
image = np.zeros((61,61))
image[0,:] = 1.
image[60,:] = 1.
image[:,0] = 1.
image[:,60] = 1.

We can draw it on the map in using:

In [7]:
m = folium.Map([37,0], zoom_start=3)

plugins.ImageOverlay(image,
                    [[0,-60],[60,60]],
                    colormap=lambda x: (1,0,0,x),
                   ).add_to(m)

m

Note that you need to provide a colormap of the form `lambda x: (R,G,B,A)` where `R,G,B,A` are floats between 0 and 1.

Now, let's try to add a line at latitude 45°, and add a polyline to verify it's well rendered.  We'll need to specify `origin='lower` to inform folium that the first lines of the array are to be plotted at the bottom of the image (see `numpy.imshow`, it's the same principle).

In [8]:
image[45,:] = 1.


m = folium.Map([37,0], zoom_start=3)

plugins.ImageOverlay(image,
                    [[0,-60],[60,60]],
                    colormap=lambda x: (1,0,0,x),
                    origin='lower',
                   ).add_to(m)

folium.PolyLine([[45,-60],[45,60]]).add_to(m)
m


But even with `origin='lower'`, the red line is not at the good latitude. This is due to Mercator projection used in Leaflet (and most other map systems).

You can read wikipedia's article on Mercator Projection (https://en.wikipedia.org/wiki/Mercator_projection), or simply let folium do the job, in precising that you want the mercator stuff to be handled.

In [9]:
m = folium.Map([37,0], zoom_start=3)

folium.PolyLine([[45,-60],[45,60]]).add_to(m)

plugins.ImageOverlay(image,
                    [[0,-60],[60,60]],
                    origin='lower',
                    colormap=lambda x: (1,0,0,x),
                    mercator_project=True,
                   ).add_to(m)

m

This time, the lines are properly positionned (at the precision of the array).

## Conclusion

That's all folks !

Hope it'll be useful to you. Don't hesitate to provide a feedback on what can be improved, which method do you prefer, etc.